## EXPERIMENT 1.1: AdaFace

In [1]:
## Load libraries

import numpy as np
import cv2
from matplotlib import pyplot as plt
import torch
import seaborn as sns
import pandas as pd
from sklearn.preprocessing import normalize
import sys
sns.set(style="white")
%matplotlib inline
sys.path.append('../../utils')
from Model_utils.Model_funcs import *
from Result_metric_utils.result_metrics import *
from Data_proc_utils.Data_proc_funcs import *
from Plotting_stats_utils.plotting_threshold import *
from Plotting_stats_utils.stats_tables import *


from IPython import embed


In [2]:
# Save figures
from matplotlib import pyplot as plt
save_fig_path = '../../figures/ada_1_1/'


### AdaFace Results

This notebook loads the feature vectors from MagFace and run them through the results metrics:
FNIR, FPIR, FND, FPD, and GARBE

In [3]:
feature_list_children = '../../data/data_full/feature_vectors/adaface_feature_vectors/1.1/similarity_scores_children_filtered_bibel_FINAL_INFERENCE_baseline1.pt'
feature_list_adults = '../../data/data_full/feature_vectors/adaface_feature_vectors/1.1/similarity_scores_adults_bibel_cropped_resized_retina_baseline1.pt'


image_names_c, ids_c, num_ids_c, norm_feats_c = load_adaface_vectors(feature_list_children, canonical = False)
image_names_a, ids_a, num_ids_a, norm_feats_a = load_adaface_vectors(feature_list_adults, canonical=False)
# image_names_a, ids_a, num_ids_a, norm_feats_a = load_adaface_vectors_adults(feature_list_adults) # virker for den gamle, men ikke de cropped af en eller anden grund

ids_a = ["_".join(x.split("_")[1:]) for x in ids_a]


# # Similarity matrices from adaface - all
# sim_mat_c = np.dot(norm_feats_c, norm_feats_c.T)
# sim_mat_a = np.dot(norm_feats_a, norm_feats_a.T)

# WORKS
# def neighborhood_aware_cosine(norm_feats, k=5):
#     # Step 1: Compute Cosine Similarity Matrix
#     cosine_sim = np.dot(norm_feats, norm_feats.T)
#     # Set diagonal to zero
#     np.fill_diagonal(cosine_sim, 0)

#     # Step 2: Apply NAC to each element
#     NAC_sim = np.zeros_like(cosine_sim)
#     num_samples = norm_feats.shape[0]

#     for i in range(num_samples):
#         # Get top-k neighbors for each probe
#         top_k_indices = np.argsort(-cosine_sim[i])[:k]
#         denominator = np.sum(np.exp(cosine_sim[i, top_k_indices]))

#         for j in range(num_samples):
#             if j in top_k_indices:
#                 NAC_sim[i, j] = np.exp(cosine_sim[i, j]) / denominator

#     return NAC_sim


import numpy as np

def neighborhood_aware_cosine(norm_feats, k=5):
    # Step 1: Compute Cosine Similarity Matrix
    cosine_sim = np.dot(norm_feats, norm_feats.T)
    # Set diagonal to zero
    np.fill_diagonal(cosine_sim, 0)

    # Step 2: Apply NAC to each element
    NAC_sim = np.zeros_like(cosine_sim)
    num_samples = norm_feats.shape[0]

    for i in range(num_samples):
        # Set self-similarity to zero
        cosine_sim[i, i] = 0
        # Get top-k neighbors for each probe
        top_k_indices = np.argsort(-cosine_sim[i])[:k]
        denominator = np.sum(np.exp(cosine_sim[i, top_k_indices]))

        for j in range(num_samples):
            if j in top_k_indices:
                NAC_sim[i, j] = np.exp(cosine_sim[i, j]) / denominator

    return NAC_sim

# Now we dont need to exlude the ones in the fnir...


sim_mat_c = neighborhood_aware_cosine(norm_feats_c, k=8)
sim_mat_a = neighborhood_aware_cosine(norm_feats_a, k=8)





# Dataframes with info, removes names not in magface results
children_all = pd.read_csv('../../data/image_info_csvs/final_filtered_children_df_BIBEL.csv')
children_all = children_all[children_all.image_name.isin(image_names_c)]

adults_all_org = pd.read_csv('../../data/image_info_csvs/final_filtered_adults_df_BIBEL.csv')
adults_all = adults_all_org[adults_all_org.image_name.isin(image_names_a)]

In [4]:
sim_mat_a.shape

AttributeError: 'NoneType' object has no attribute 'shape'

In [41]:
sim_mat_a[0]

array([0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.     

In [16]:
image_names_a[0] # har 1 billede

'm.012mh__0004'

In [17]:
image_names_a[2]

'm.012mmb_0001'

In [18]:
np.set_printoptions(threshold=sys.maxsize)

def most_find(sequence, n):
    lst = sorted(range(len(sequence)), key=lambda x:sequence[x], reverse=True)
    return lst[:n]

result = most_find(sim_mat_a_d[2], 10)

print(sim_mat_a_d[2][result])


[0.18897931 0.10510295 0.0910849  0.0883004  0.08811365 0.08784649
 0.08776895 0.08764133 0.0876045  0.08755753]


In [20]:
np.set_printoptions(threshold=sys.maxsize)

def most_find(sequence, n):
    lst = sorted(range(len(sequence)), key=lambda x:sequence[x], reverse=True)
    return lst[:n]

result = most_find(sim_mat_a_o[2], 10)

print(sim_mat_a_o[2][result])



[1.0000002  0.41330305 0.27015477 0.2391074  0.23699012 0.2339536
 0.23307052 0.23161542 0.23119503 0.23065883]


In [19]:

# # Similarity matrices from adaface - all
sim_mat_c_o = np.dot(norm_feats_c, norm_feats_c.T)
sim_mat_a_o = np.dot(norm_feats_a, norm_feats_a.T)


In [9]:
feature_list_children = '../../data/data_full/feature_vectors/adaface_feature_vectors/1.1/similarity_scores_children_filtered_bibel_FINAL_INFERENCE_baseline1.pt'
feature_list_adults = '../../data/data_full/feature_vectors/adaface_feature_vectors/1.1/similarity_scores_adults_bibel_cropped_resized_retina_baseline1.pt'


image_names_c, ids_c, num_ids_c, norm_feats_c = load_adaface_vectors(feature_list_children, canonical = False)
image_names_a, ids_a, num_ids_a, norm_feats_a = load_adaface_vectors(feature_list_adults, canonical=False)
# image_names_a, ids_a, num_ids_a, norm_feats_a = load_adaface_vectors_adults(feature_list_adults) # virker for den gamle, men ikke de cropped af en eller anden grund

ids_a = ["_".join(x.split("_")[1:]) for x in ids_a]


# # Similarity matrices from adaface - all
# sim_mat_c = np.dot(norm_feats_c, norm_feats_c.T)
# sim_mat_a = np.dot(norm_feats_a, norm_feats_a.T)


def neighborhood_aware_cosine(norm_feats, k=5):
    # Step 1: Compute Cosine Similarity Matrix
    cosine_sim = np.dot(norm_feats, norm_feats.T)
    # Set diagonal to zero
    #np.fill_diagonal(cosine_sim, 0)

    # Step 2: Apply NAC to each element
    NAC_sim = np.zeros_like(cosine_sim)
    num_samples = norm_feats.shape[0]

    for i in range(num_samples):
        # Get top-k neighbors for each probe
        top_k_indices = np.argsort(-cosine_sim[i])[:k]
        denominator = np.sum(np.exp(cosine_sim[i, top_k_indices]))

        for j in range(num_samples):
            if j in top_k_indices:
                NAC_sim[i, j] = np.exp(cosine_sim[i, j]) / denominator

    return NAC_sim

sim_mat_c_d_8 = neighborhood_aware_cosine(norm_feats_c, k=8)
sim_mat_a_d_8 = neighborhood_aware_cosine(norm_feats_a, k=8)





# Dataframes with info, removes names not in magface results
children_all = pd.read_csv('../../data/image_info_csvs/final_filtered_children_df_BIBEL.csv')
children_all = children_all[children_all.image_name.isin(image_names_c)]

adults_all_org = pd.read_csv('../../data/image_info_csvs/final_filtered_adults_df_BIBEL.csv')
adults_all = adults_all_org[adults_all_org.image_name.isin(image_names_a)]

In [21]:
np.set_printoptions(threshold=sys.maxsize)

def most_find(sequence, n):
    lst = sorted(range(len(sequence)), key=lambda x:sequence[x], reverse=True)
    return lst[:n]

result = most_find(sim_mat_a_d_8[2], 10)

print(sim_mat_a_d_8[2][result])


[0.22911084 0.12742256 0.11042763 0.10705182 0.10682541 0.10650151
 0.10640751 0.10625279 0.         0.        ]


In [10]:
feature_list_children = '../../data/data_full/feature_vectors/adaface_feature_vectors/1.1/similarity_scores_children_filtered_bibel_FINAL_INFERENCE_baseline1.pt'
feature_list_adults = '../../data/data_full/feature_vectors/adaface_feature_vectors/1.1/similarity_scores_adults_bibel_cropped_resized_retina_baseline1.pt'


image_names_c, ids_c, num_ids_c, norm_feats_c = load_adaface_vectors(feature_list_children, canonical = False)
image_names_a, ids_a, num_ids_a, norm_feats_a = load_adaface_vectors(feature_list_adults, canonical=False)
# image_names_a, ids_a, num_ids_a, norm_feats_a = load_adaface_vectors_adults(feature_list_adults) # virker for den gamle, men ikke de cropped af en eller anden grund

ids_a = ["_".join(x.split("_")[1:]) for x in ids_a]


# # Similarity matrices from adaface - all
# sim_mat_c = np.dot(norm_feats_c, norm_feats_c.T)
# sim_mat_a = np.dot(norm_feats_a, norm_feats_a.T)


def neighborhood_aware_cosine(norm_feats, k=5):
    # Step 1: Compute Cosine Similarity Matrix
    cosine_sim = np.dot(norm_feats, norm_feats.T)
    # Set diagonal to zero
    np.fill_diagonal(cosine_sim, 0)

    # Step 2: Apply NAC to each element
    NAC_sim = np.zeros_like(cosine_sim)
    num_samples = norm_feats.shape[0]

    for i in range(num_samples):
        # Get top-k neighbors for each probe
        top_k_indices = np.argsort(-cosine_sim[i])[:k]
        denominator = np.sum(np.exp(cosine_sim[i, top_k_indices]))

        for j in range(num_samples):
            if j in top_k_indices:
                NAC_sim[i, j] = np.exp(cosine_sim[i, j]) / denominator

    return NAC_sim

sim_mat_c_no_d_8 = neighborhood_aware_cosine(norm_feats_c, k=8)
sim_mat_a_no_d_8 = neighborhood_aware_cosine(norm_feats_a, k=8)





# Dataframes with info, removes names not in magface results
children_all = pd.read_csv('../../data/image_info_csvs/final_filtered_children_df_BIBEL.csv')
children_all = children_all[children_all.image_name.isin(image_names_c)]

adults_all_org = pd.read_csv('../../data/image_info_csvs/final_filtered_adults_df_BIBEL.csv')
adults_all = adults_all_org[adults_all_org.image_name.isin(image_names_a)]

In [22]:
np.set_printoptions(threshold=sys.maxsize)

def most_find(sequence, n):
    lst = sorted(range(len(sequence)), key=lambda x:sequence[x], reverse=True)
    return lst[:n]

result = most_find(sim_mat_a_no_d_8[2], 10)

print(sim_mat_a_no_d_8[2][result])

[0.14527754 0.12590122 0.12205238 0.12179424 0.12142497 0.12131778
 0.12114138 0.12109047 0.         0.        ]


In [50]:
np.set_printoptions(threshold=sys.maxsize)

def most_find(sequence, n):
    lst = sorted(range(len(sequence)), key=lambda x:sequence[x], reverse=True)
    return lst[:n]

result = most_find(sim_mat_a_o[0], 10)

print(sim_mat_a_o[0][result])

[1.0000002  0.33835357 0.30671042 0.27907413 0.27471066 0.2711722
 0.26657024 0.2622811  0.26140794 0.24996573]


# Finding the right threshold

In [21]:
## Function for calculating FNIR
## Function for calculating FNIR
def compute_fnir_h(enrolled_sim_mat, sim_mat, enrolled_ids, enrolled_num_id, ids, thold=0.5):
    """
    FNIR formula from ISO standard ISO/IEC 19795-1:2021
    ids: unique ids for all images in results
    enrolled_ids: ids for the enrolled images
    enrolled_sim_mat: enrolled similarity matrix
    sim_mat: all similarity scores
    """
    # M_D: set of mated identification transactions with reference database. - i.e. there can be multiple ids?
    M_d_set = set(enrolled_ids)
    M_d_set_len = len(enrolled_sim_mat)
    neg_ref = 0

    # For each id corresponding to the id in the set, check if one of it's corresponding ids are above threshold

    # Get enrolled similarity scores
    enrolled_sim_scores = []

    ## Iterate over each enrolled reference for transaction i
    for m_i, id_now in enumerate(ids):
        # Check if the identity is enrolled
        if id_now in M_d_set:
            mated_ids_exact = [id == id_now for id in ids] # Array of true and falses
            mated_sim_scores_slice = sim_mat[m_i] # Row corresponding to the enrolled probe id
            mated_sim_scores_slice_slice = [value for value, keep in zip(mated_sim_scores_slice, mated_ids_exact) if keep] #Only enrolled similarity scores for the same ids corresponding to the probe id
            enrolled_sim_scores.extend(mated_sim_scores_slice_slice)

    # Iterate over each enrolled reference for transaction i
    for i in range(M_d_set_len):
        probe = enrolled_num_id[i] # numerical id by magface, e.g. str value "African_244" becomes num. value 35.

        # Check if the reference probe id is in negative list/below threshold
        classified_negative_list = enrolled_sim_mat[i] <= thold
        classified_negative_idx = list(np.where(classified_negative_list)[0])  # Get indexes where the score is below threshold
        face_idx_neg_class = enrolled_num_id[classified_negative_idx]  # Get numerical ids in the negative class
        # If numerical id in negative list is equal to the probe id, count 1
        if probe in face_idx_neg_class:
            neg_ref += 1

    # Calculate FNIR
    fnir = neg_ref / M_d_set_len

    enrolled_sim_scores_final = np.array(enrolled_sim_scores)
    enrolled_sim_scores_final = enrolled_sim_scores_final[enrolled_sim_scores_final<0.999]
     #we hae removed 'ones' earlier
    # i = 0
    # while len(enrolled_sim_scores_final) > (len(enrolled_sim_scores)-len(enrolled_ids)):
    #     i += 0.00
    #     print("NOT SAME LENGTH", len(enrolled_sim_scores_final), len(enrolled_sim_scores)-len(enrolled_ids))
    #     enrolled_sim_scores_final = enrolled_sim_scores_final[enrolled_sim_scores_final<0.999+i]

    return fnir, enrolled_sim_scores_final

In [23]:
def compute_metrics_ex_1_1_h(random_states, percentiles, children_all, adults_all, image_names_c, image_names_a, sim_mat_c, sim_mat_a, num_ids_c, num_ids_a, ids_c, ids_a, balance_child_data, balance_adults_data_enrolled, compute_fnir, compute_fpir, GARBE):
    FNIR_c_list = []
    FNIR_a_list = []
    FPIR_c_list = []
    FPIR_a_list = []
    FPD_list = []
    FND_list = []
    GARBE_list = []
    threshold_list = []

    for random_state_i in random_states:
        # Load children and adults balanced data
        children_balanced_df_i = balance_child_data(children_all, print_stats=False, random_state=random_state_i)
        adults_balanced_df_i = balance_adults_data_enrolled(children_balanced_df_i, adults_all, print_stats=False, random_state=random_state_i)

        # All reference image names, enrolled and non-enrolled image names - children
        c_mates = children_balanced_df_i.groupby("identity_name").agg({'identity_name': ['count']})
        enrolled_identity_names_c = c_mates[c_mates[('identity_name', 'count')] > 1].index
        enrolled_image_names_c = list(children_balanced_df_i[children_balanced_df_i["identity_name"].isin(enrolled_identity_names_c)].image_name)
        non_enrolled_identity_names_c = c_mates[c_mates[('identity_name', 'count')] == 1].index
        non_enrolled_image_names_c = list(children_balanced_df_i[children_balanced_df_i["identity_name"].isin(non_enrolled_identity_names_c)].image_name)
        all_reference_image_names_c = list(children_balanced_df_i.image_name)

        # All reference image names, enrolled and non-enrolled image names - adults
        a_mates = adults_balanced_df_i.groupby("identity_name").agg({'identity_name': ['count']})
        enrolled_identity_names_a = a_mates[a_mates[('identity_name', 'count')] > 1].index
        enrolled_image_names_a = list(adults_balanced_df_i[adults_balanced_df_i["identity_name"].isin(enrolled_identity_names_a)].image_name)
        non_enrolled_identity_names_a = a_mates[a_mates[('identity_name', 'count')] == 1].index
        non_enrolled_image_names_a = list(adults_balanced_df_i[adults_balanced_df_i["identity_name"].isin(non_enrolled_identity_names_a)].image_name)
        all_reference_image_names_a = list(adults_balanced_df_i.image_name)

        # Similarity matrices for ids in reference database
        indices_c_all_reference = [image_names_c.index(name) for name in all_reference_image_names_c]
        indices_a_all_reference = [image_names_a.index(name) for name in all_reference_image_names_a]

        # Extract corresponding columns from the similarity matrix
        sim_mat_c_reference_cols = sim_mat_c[:, indices_c_all_reference]
        sim_mat_a_reference_cols = sim_mat_a[:, indices_a_all_reference]

        # Extract corresponding rows from the numerical ids
        num_ids_c_reference = num_ids_c[indices_c_all_reference]
        num_ids_a_reference = num_ids_a[indices_a_all_reference]

        # Similarity matrices for non-enrolled ids
        indices_c_non_enrolled = [image_names_c.index(name) for name in non_enrolled_image_names_c]
        indices_a_non_enrolled = [image_names_a.index(name) for name in non_enrolled_image_names_a]

        sim_mat_c_non_enrolled_0 = sim_mat_c_reference_cols[indices_c_non_enrolled]
        sim_mat_a_non_enrolled_0 = sim_mat_a_reference_cols[indices_a_non_enrolled]

        num_ids_c_non_enrolled = num_ids_c[indices_c_non_enrolled]
        num_ids_a_non_enrolled = num_ids_a[indices_a_non_enrolled]

        # Similarity matrices for enrolled ids
        indices_c_enrolled = [image_names_c.index(name) for name in enrolled_image_names_c]
        indices_a_enrolled = [image_names_a.index(name) for name in enrolled_image_names_a]

        sim_mat_c_enrolled_0 = sim_mat_c[np.ix_(indices_c_enrolled, indices_c_enrolled)]
        sim_mat_a_enrolled_0 = sim_mat_a[np.ix_(indices_a_enrolled, indices_a_enrolled)]

        num_ids_c_enrolled = num_ids_c[indices_c_enrolled]
        num_ids_a_enrolled = num_ids_a[indices_a_enrolled]

        for percentile in percentiles:
            # thold = (np.percentile(sim_mat_c, percentile) + np.percentile(sim_mat_a, percentile)) / 2
            thold = percentile

            # Evaluation metrics
            FNIR_c, sim_mat_c_enrolled = compute_fnir(sim_mat_c_enrolled_0, sim_mat_c, enrolled_identity_names_c, num_ids_c_enrolled, ids_c, thold=thold)
            FNIR_a, sim_mat_a_enrolled = compute_fnir(sim_mat_a_enrolled_0, sim_mat_a, enrolled_identity_names_a, num_ids_a_enrolled, ids_a, thold=thold)

            FPIR_c = compute_fpir(sim_mat_c_non_enrolled_0, num_ids_c_non_enrolled, num_ids_c_reference, thold=thold)
            FPIR_a = compute_fpir(sim_mat_a_non_enrolled_0, num_ids_a_non_enrolled, num_ids_a_reference, thold=thold)

            alpha_garbe = 0.25
            FPD_i, FND_i, GARBE_i = GARBE(FNIR_c, FNIR_a, FPIR_c, FPIR_a, alpha=alpha_garbe)

            FNIR_c_list.append(FNIR_c)
            FNIR_a_list.append(FNIR_a)
            FPIR_c_list.append(FPIR_c)
            FPIR_a_list.append(FPIR_a)
            FPD_list.append(FPD_i)
            FND_list.append(FND_i)
            GARBE_list.append(GARBE_i)
            threshold_list.append(thold)

            print(f"Done for random_state: {random_state_i}, percentile: {percentile}")

    data = {
        'Iteration': np.repeat(random_states, len(percentiles)),
        'Percentile': percentiles * len(random_states),
        'FNIR_c': FNIR_c_list,
        'FNIR_a': FNIR_a_list,
        'FPIR_c': FPIR_c_list,
        'FPIR_a': FPIR_a_list,
        'FPD': FPD_list,
        'FND': FND_list,
        'GARBE': GARBE_list,
        'Threshold': threshold_list
    }

    df_all_threshold_x = pd.DataFrame(data)

    return df_all_threshold_x

In [24]:
random_states = [1]
percentiles = np.arange(0.0, 1.0, 0.01).tolist()

df_all_threshold_x = compute_metrics_ex_1_1_h(random_states, percentiles, children_all, adults_all, image_names_c, image_names_a, sim_mat_c, sim_mat_a, num_ids_c, num_ids_a, ids_c, ids_a, balance_child_data, balance_adults_data_enrolled, compute_fnir_h, compute_fpir, GARBE)


NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 15162 14367
NOT SAME LENGTH 1516

KeyboardInterrupt: 

In [ ]:

plot_threshold_metrics_ex_1_1_together_w_conf(df_all_threshold_x,  'AdaFace ex. 1.1', save_fig_path)


# Stats

In [ ]:

random_states = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]

df_all_results, sim_mat_dict_all_magface_ex1_1 = evaluate_metrics_ex_1_1(
    random_states, children_all, adults_all, image_names_c, image_names_a,
    sim_mat_c, sim_mat_a, num_ids_c, num_ids_a, ids_c, ids_a, balance_child_data,
    balance_adults_data_enrolled, compute_fnir, compute_fpir, GARBE, remove_ones, df_all_threshold_x[df_all_threshold_x.FNIR_c <0.05].Threshold.max()
)

df_all_results.describe().applymap(lambda x: f"{x:.3f}")

In [ ]:
# Generate the LaTeX table
latex_table = generate_latex_table(df_all_results.applymap(lambda x: f"{x:.3f}").drop(columns='Iteration'))
print(latex_table)


In [ ]:
latex_table = generate_latex_table(df_all_results.describe().applymap(lambda x: f"{x:.3f}").drop(columns='Iteration'))
print(latex_table)

In [ ]:
df_all_results.to_csv('df_all_results_ada_1_1.csv', index=False)


# Stats

In [ ]:
t_statistic, p_value = stats.ttest_rel(df_all_results['FNIR_c'], df_all_results['FNIR_a'])

# Output the results
print(f'T-statistic: {t_statistic}')
print(f'P-value: {p_value}')

# Gemmer simscores

In [ ]:

sim_mat_c_enrolled_iterations = []

# Loop to access each array and append it to the list
for i in range(1, 11):
    key = f'sim_mat_c_enrolled_iteration_{i}'
    if key in sim_mat_dict_all_magface_ex1_1:
        sim_mat_c_enrolled_iterations.append(sim_mat_dict_all_magface_ex1_1[key])

# Concatenate all arrays into one big array
sim_mat_c_enrolled_iterations_all = np.concatenate(sim_mat_c_enrolled_iterations)
sim_mat_c_enrolled_iterations_all = pd.DataFrame(sim_mat_c_enrolled_iterations_all)
sim_mat_c_enrolled_iterations_all.to_csv('sim_mat_c_enrolled_iterations_all_ada.csv', index=False)
# Print the big array
print(len(sim_mat_c_enrolled_iterations_all))

sim_mat_a_enrolled_iterations = []

# Loop to access each array and append it to the list
for i in range(1, 11):
    key = f'sim_mat_a_enrolled_iteration_{i}'
    if key in sim_mat_dict_all_magface_ex1_1:
        sim_mat_a_enrolled_iterations.append(sim_mat_dict_all_magface_ex1_1[key])

# Concatenate all arrays into one big array
sim_mat_a_enrolled_iterations_all = np.concatenate(sim_mat_a_enrolled_iterations)
sim_mat_a_enrolled_iterations_all = pd.DataFrame(sim_mat_a_enrolled_iterations_all)
sim_mat_a_enrolled_iterations_all.to_csv('sim_mat_a_enrolled_iterations_all_ada.csv', index=False)


# Print the big array
print(len(sim_mat_a_enrolled_iterations_all))

sim_mat_c_non_enrolled_iterations = []

# Loop to access each array and append it to the list
for i in range(1, 11):
    key = f'sim_mat_c_non_enrolled_iteration_{i}'
    if key in sim_mat_dict_all_magface_ex1_1:
        sim_mat_c_non_enrolled_iterations.append(sim_mat_dict_all_magface_ex1_1[key])

sim_mat_c_non_enrolled_iterations_all = np.concatenate(sim_mat_c_non_enrolled_iterations)
sim_mat_c_non_enrolled_iterations_all = pd.DataFrame(sim_mat_c_non_enrolled_iterations_all)
sim_mat_c_non_enrolled_iterations_all.to_csv('sim_mat_c_non_enrolled_iterations_all_ada.csv', index=False)
# Print the big array
print(len(sim_mat_c_non_enrolled_iterations_all))


sim_mat_a_non_enrolled_iterations = []

# Loop to access each array and append it to the list
for i in range(1, 11):
    key = f'sim_mat_a_non_enrolled_iteration_{i}'
    if key in sim_mat_dict_all_magface_ex1_1:
        sim_mat_a_non_enrolled_iterations.append(sim_mat_dict_all_magface_ex1_1[key])

sim_mat_a_non_enrolled_iterations_all = np.concatenate(sim_mat_a_non_enrolled_iterations)
sim_mat_a_non_enrolled_iterations_all = pd.DataFrame(sim_mat_a_non_enrolled_iterations_all)
sim_mat_a_non_enrolled_iterations_all.to_csv('sim_mat_a_non_enrolled_iterations_all_ada.csv', index=False)

# Print the big array
print(len(sim_mat_a_non_enrolled_iterations_all))


# Loader sim scores

In [ ]:
sim_mat_c_enrolled_iterations_all_ada = (pd.read_csv('sim_mat_c_enrolled_iterations_all_ada.csv')).values.flatten()
sim_mat_a_enrolled_iterations_all_ada = (pd.read_csv('sim_mat_a_enrolled_iterations_all_ada.csv')).values.flatten()
sim_mat_c_non_enrolled_iterations_all_ada = (pd.read_csv('sim_mat_c_non_enrolled_iterations_all_ada.csv')).values.flatten()
sim_mat_a_non_enrolled_iterations_all_ada = (pd.read_csv('sim_mat_a_non_enrolled_iterations_all_ada.csv')).values.flatten()


In [ ]:
from scipy.stats import describe, gaussian_kde
import math

def descriptive_statistics(mated_scores, nonmated_scores):
    stats_labels = ["Observations", "Minimum", "Maximum", "Mean", "St. Dev.", "Skewness", "Ex. Kurtosis"]
    mated_stats = describe(mated_scores)
    mated_stats = [mated_stats.nobs, mated_stats.minmax[0], mated_stats.minmax[1], mated_stats.mean, math.sqrt(mated_stats.variance), mated_stats.skewness, mated_stats.kurtosis]
    nonmated_stats = describe(nonmated_scores)
    nonmated_stats = [nonmated_stats.nobs, nonmated_stats.minmax[0], nonmated_stats.minmax[1], nonmated_stats.mean, math.sqrt(nonmated_stats.variance), nonmated_stats.skewness, nonmated_stats.kurtosis]

    stats_system_df = pd.DataFrame(np.array([stats_labels, mated_stats, nonmated_stats]).T, columns=["Statistic", "Mated", "Non-mated"])
    stats_system_df = stats_system_df.astype({"Statistic": str, "Mated": float, "Non-mated": float})
    return stats_system_df

In [ ]:
mated_scores1 = sim_mat_a_enrolled_iterations_all_ada
nonmated_scores1 = sim_mat_a_non_enrolled_iterations_all_ada
scores_type1 = "similarity"
stats_system1_df = descriptive_statistics(mated_scores1, nonmated_scores1)
display(stats_system1_df)

In [ ]:
mated_scores2 = sim_mat_c_enrolled_iterations_all_ada
nonmated_scores2 = sim_mat_c_non_enrolled_iterations_all_ada
scores_type2 = "similarity"
stats_system2_df = descriptive_statistics(mated_scores2, nonmated_scores2)
display(stats_system2_df)

In [ ]:
mated_colour = "green"
mated_label = "Mated scores"
nonmated_colour = "red"
nonmated_label = "Non-mated scores"

figure_size = (12,6)
alpha_shade = 0.25
alpha_fill = 1.0
linewidth = 2
legend_loc = "upper left"
legend_anchor = (1.0, 1.02)
legend_cols = 1
legend_fontsize = 12
label_fontsize = 16

threshold_colour = "black"
threshold_style = "--"
round_digits = 5
sns.set(style="white", palette="muted", color_codes=True)
plt.rc("axes", axisbelow=True)

In [ ]:

import matplotlib.pyplot as plt
import numpy as np

def plot_histogram(mated_scores, nonmated_scores, normalise=True, savename=None, title="Histogram"):
    def normalise_scores(distribution):
        return np.ones_like(distribution) / len(distribution)

    mated_mean = np.mean(mated_scores)

    plt.figure(figsize=(10, 6))  # Replace 'figure_size' with a specific size if not defined

    if normalise:
        plt.hist(mated_scores, bins=50, weights=normalise_scores(mated_scores), color='green', alpha=0.5, label='Mated Scores')  # Replace 'mated_label' with 'Mated Scores'
        plt.hist(nonmated_scores, bins=30, weights=normalise_scores(nonmated_scores), color='red', alpha=0.5, label='Non-mated Scores')  # Replace 'nonmated_label' with 'Non-mated Scores'
        ylabel = "Probability Density"
    else:
        plt.hist(mated_scores, bins=50, color='green', alpha=0.5, label='Mated Scores')
        plt.hist(nonmated_scores, bins=30, color='red', alpha=0.5, label='Non-mated Scores')
        ylabel = "Count"

    plt.axvline(mated_mean, color='darkgreen', linestyle='--', linewidth=2, label=f'Mated Mean: {mated_mean:.2f}')

    plt.xlabel("Comparison Score", size=16)
    plt.ylabel(ylabel, size=16)
    plt.title(title, size=20)
    plt.grid(True)
    plt.legend(loc='upper right', bbox_to_anchor=(1, 1), ncol=1, fontsize=14)  # Adjust legend parameters as needed

    if savename is not None:
        plt.savefig(savename, bbox_inches="tight")
        plt.cla()
        plt.clf()
        plt.close()
    else:
        plt.show()


In [ ]:

plot_histogram(mated_scores1, nonmated_scores1, normalise=True, title = 'Adults - AdaFace ex. 1.1 ', save_fig_path=save_fig_path)


In [ ]:
plot_histogram(mated_scores2, nonmated_scores2, normalise=True, title = 'Children - AdaFace ex. 1.1 ', save_fig_path=save_fig_path)


# DET curves


In [ ]:
from DET_utils.DET_plots import *

In [ ]:
d_prime_system1 = d_prime(mated_scores1, nonmated_scores1)
print("d' child =", round(d_prime_system1, round_digits))

d_prime_system2 = d_prime(mated_scores2, nonmated_scores2)
print("d' adult =", round(d_prime_system2, round_digits))


In [ ]:
threshold1 = df_all_threshold_x[df_all_threshold_x.FNIR_c <0.05].Threshold.max()
kde_with_threshold(mated_scores1, nonmated_scores1, scores_type1, threshold1, save_fig_path=save_fig_path, title='Adults - AdaFace ex. 1.1')

In [ ]:
threshold2 = df_all_threshold_x[df_all_threshold_x.FNIR_c <0.05].Threshold.max()
kde_with_threshold(mated_scores2, nonmated_scores2, scores_type2, threshold2, save_fig_path=save_fig_path, title='Children - AdaFace ex. 1.1')

In [ ]:
def DET_plotting_1_1(title = 'Adults vs Children - MagFace ex. 2.2', save_fig_path= 'save_fig_path'):
    figure_size = (12,7)
    alpha_shade = 0.25
    alpha_fill = 1.0
    linewidth = 2
    legend_loc = "upper left"
    legend_anchor = (1.0, 1.02)
    legend_cols = 1
    legend_fontsize = 18
    label_fontsize = 18
    tick_fontsize = 18
    system_name1 = 'Adults'
    system_name2 = 'Children'

    det = DET(biometric_evaluation_type='identification', abbreviate_axes=True, plot_eer_line=True, plot_title=title)
    det.x_limits = np.array([1e-5, .8])
    det.y_limits = np.array([1e-5, .8])
    det.x_ticks = np.array([1e-4, 1e-3, 1e-2, 5e-2, 20e-2, 40e-2, 80e-2])
    det.x_ticklabels = np.array(['0.01','0.1', '1', '5', '20', '40', '80'])
    det.y_ticks = np.array([1e-4, 1e-3, 1e-2, 5e-2, 20e-2, 40e-2, 80e-2])
    det.y_ticklabels = np.array(['0.01','0.1', '1', '5', '20', '40', '80'])
    det.create_figure()
    det.plot(tar=adjust_scores_for_DET(mated_scores1, scores_type1), non=adjust_scores_for_DET(nonmated_scores1, scores_type1), label=system_name1)
    det.plot(tar=adjust_scores_for_DET(mated_scores2, scores_type2), non=adjust_scores_for_DET(nonmated_scores2, scores_type2), label=system_name2)
    det.legend_on(loc="upper right")


DET_plotting_1_1('Adults vs Children - AdaFace ex. 1.1', save_fig_path= save_fig_path)